# Duomenų mokslas debesyje: „Azure ML SDK“ būdas

## Įvadas

Šiame užrašų knygelėje išmoksime, kaip naudoti „Azure ML SDK“, kad galėtume treniruoti, diegti ir naudoti modelį per „Azure ML“.

Būtinos sąlygos:
1. Jūs sukūrėte „Azure ML“ darbo sritį.
2. Jūs įkėlėte [Širdies nepakankamumo duomenų rinkinį](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) į „Azure ML“.
3. Jūs įkėlėte šią užrašų knygelę į „Azure ML Studio“.

Tolimesni žingsniai:

1. Sukurti eksperimentą esamoje darbo srityje.
2. Sukurti skaičiavimo klasterį.
3. Įkelti duomenų rinkinį.
4. Konfigūruoti AutoML naudojant AutoMLConfig.
5. Paleisti AutoML eksperimentą.
6. Išnagrinėti rezultatus ir gauti geriausią modelį.
7. Užregistruoti geriausią modelį.
8. Diegti geriausią modelį.
9. Naudoti galutinį tašką.

## Specifiniai „Azure Machine Learning SDK“ importai


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## Inicializuoti Darbo Aplinką
Inicializuokite darbo aplinkos objektą iš išsaugotos konfigūracijos. Įsitikinkite, kad konfigūracijos failas yra .\config.json


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## Sukurkite Azure ML eksperimentą

Sukurkime eksperimentą, pavadintą 'aml-experiment', darbo aplinkoje, kurią ką tik inicializavome.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## Sukurkite skaičiavimo klasterį  
Jums reikės sukurti [skaičiavimo tikslą](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target) savo AutoML vykdymui.


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## Duomenys
Įsitikinkite, kad įkėlėte duomenų rinkinį į Azure ML ir kad raktas turi tą patį pavadinimą kaip duomenų rinkinys.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

## AutoML konfigūracija


In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

## AutoML vykdymas


In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## Įdiegti geriausią modelį

Paleiskite šį kodą, kad įdiegtumėte geriausią modelį. Diegimo būseną galite peržiūrėti Azure ML portale. Šis žingsnis gali užtrukti kelias minutes.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## Naudokite galinį tašką
Galite pridėti įvesties duomenis prie pateikto įvesties pavyzdžio.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**Atsakomybės apribojimas**:  
Šis dokumentas buvo išverstas naudojant AI vertimo paslaugą [Co-op Translator](https://github.com/Azure/co-op-translator). Nors siekiame tikslumo, prašome atkreipti dėmesį, kad automatiniai vertimai gali turėti klaidų ar netikslumų. Originalus dokumentas jo gimtąja kalba turėtų būti laikomas autoritetingu šaltiniu. Kritinei informacijai rekomenduojama naudoti profesionalų žmogaus vertimą. Mes neprisiimame atsakomybės už nesusipratimus ar klaidingus interpretavimus, atsiradusius dėl šio vertimo naudojimo.
